In [5]:

import s3fs
import pandas
import polars as pl
import pyarrow.dataset as ds

fs = s3fs.S3FileSystem(profile="aws_profile_name")
bucket = "<S3_BUCKET_NAME>"
path = "<S3_PATH>/partition=<S3_PARTITION>"

s3_endpoint = f"s3://{bucket}/{path}"

myds = ds.dataset([y for y in fs.ls(s3_endpoint) if ".parquet" in y], filesystem=fs)
lazy_df = pl.scan_ds(myds)

df = lazy_df.select(pl.col('*')).collect()

print(df)

AttributeError: 'S3' object has no attribute 'Session'

In [ ]:
import boto3
import polars as pl


# Your MinIO/S3 credentials and bucket details
endpoint_url = 'http://localhost:9000'  # Your MinIO endpoint
access_key = 'minio_debug'
secret_key = 'minio123'
bucket_name = 'depictio-bucket'
object_key = '64a842842bf4fa7deaa3dbed'  # The name of the file you want to read

# Create an S3 client
s3_client = boto3.client('s3',
                         endpoint_url=endpoint_url,
                         aws_access_key_id=access_key,
                         aws_secret_access_key=secret_key,
                         region_name='us-east-1')  # Region name can be any string

session = boto3.session.Session()
credentials = session.get_credentials()

df = pl.scan_parquet(
    "s3://coiled-data/uber/*.parquet",
    storage_options={
        "aws_access_key_id": credentials.access_key,
        "aws_secret_access_key": credentials.secret_key,
        "region": "us-east-2",
        "session_token": credentials.token,
    },
)

In [2]:
import os
import polars as pl

# Set environment variables for MinIO access
# os.environ["AWS_ACCESS_KEY_ID"] = "DSj0vuC7bfMUGZpX2L4h"
# os.environ["AWS_SECRET_ACCESS_KEY"] = "wQ4OGBfXDwBV0nXuW0cHQfPqSDfhMOKUqi3kjtLU"
os.environ["AWS_ACCESS_KEY_ID"] = "minio"
os.environ["AWS_SECRET_ACCESS_KEY"] = "minio123"
os.environ["AWS_S3_ENDPOINT_URL"] = "http://localhost:9000"
os.environ["AWS_REGION"] = "us-east-1"


# Now attempt to read the Delta table
location = "depictio-bucket/64a842842bf4fa7deaa3dbed/65ce3104c7b669e4fd4f5165/65ce3104c7b669e4fd4f5166/0-1190282a-64f2-4ecf-b043-8928261afb0c-0.parquet"
df = pl.read_parquet(f"s3://{location}", storage_options=)
df


ComputeError: Generic S3 error: Client error with status 403 Forbidden: No Body

In [4]:
import s3fs
fs = s3fs.S3FileSystem()  
fs.

In [4]:
import polars as pl
import s3fs

storage_options = {
    "AWS_ACCESS_KEY_ID": "minio",
    "AWS_SECRET_ACCESS_KEY": "minio123",
    "AWS_S3_ENDPOINT_URL": "http://localhost:9000",
    "AWS_REGION": "us-east-1",
}
#conn_data = { 'key': 'minio', 'secret': 'minio123', 'client_kwargs': { 'endpoint_url': 'http://localhost:9000' }}
#fs = s3fs.S3FileSystem(**conn_data)
#fs
location = "depictio-bucket/64a842842bf4fa7deaa3dbed/65ce3104c7b669e4fd4f5165/65ce3104c7b669e4fd4f5166/0-1190282a-64f2-4ecf-b043-8928261afb0c-0.parquet"

df = pl.read_parquet(f"http://{location}", storage_options=storage_options)
df


OSError: Generic S3 error: Client error with status 403 Forbidden: <?xml version="1.0" encoding="UTF-8"?>
<Error><Code>InvalidAccessKeyId</Code><Message>The AWS Access Key Id you provided does not exist in our records.</Message><AWSAccessKeyId>minio</AWSAccessKeyId><RequestId>MAKE85BK126VW274</RequestId><HostId>pq87U+6yQEY+x4Uc2Wp1I8hPIhZ6kWP20NWulGynb5iBVuNM09ovN5e3jF/LjV0vzurdYYndsT0=</HostId></Error>

In [6]:
import boto3
from botocore.exceptions import NoCredentialsError

# Your MinIO/S3 credentials and bucket details
endpoint_url = 'http://localhost:9000'  # Your MinIO endpoint
access_key = 'minio_debug'
secret_key = 'minio123'
bucket_name = 'depictio-bucket'
object_key = '64a842842bf4fa7deaa3dbed'  # The name of the file you want to read

# Create an S3 client
s3_client = boto3.client('s3',
                         endpoint_url=endpoint_url,
                         aws_access_key_id=access_key,
                         aws_secret_access_key=secret_key,
                         region_name='us-east-1')  # Region name can be any string


In [ ]:
try:
    file_content = s3_client.get_object(Bucket=bucket_name, Key=object_key)['Body'].read()
    print(file_content.decode('utf-8'))  # Assuming the file is text-based; decode as necessary
except NoCredentialsError:
    print("Credentials not available")
except Exception as e:
    print(e)


In [19]:
from io import BytesIO
import boto3
import polars as pl

# MinIO/S3 credentials and bucket details
endpoint_url = 'http://localhost:9000'  # Your MinIO endpoint
access_key = 'minio'
secret_key = 'minio123'
bucket_name = 'depictio-bucket'
object_key = '64a842842bf4fa7deaa3dbed/65c4ef0f26d99f46c993a5af/65c4ef0f26d99f46c993a5b0/1-ea34b2f8-4b6c-455f-b3ca-1ae0519c792f-0.parquet'  # Name of your parquet file

# Create S3 client
s3_client = boto3.client(
    's3',
    endpoint_url=endpoint_url,
    aws_access_key_id=access_key,
    aws_secret_access_key=secret_key
)

# Access object using S3 client
obj = s3_client.get_object(Bucket=bucket_name, Key=object_key)

# Retrieve the Parquet file as a bytes stream
try:
    obj = s3_client.get_object(Bucket=bucket_name, Key=object_key)
    data = obj['Body'].read()
    
    # Use BytesIO to convert bytes data to a file-like object for pandas
    data_stream = BytesIO(data)
    
    # Use pandas to read the Parquet file
    df = pl.read_parquet(data_stream)
    print(df)
except boto3.exceptions.Boto3Error as e:
    print(f"An error occurred: {e}")

shape: (6_720, 15)
┌──────────────┬────────────┬─────────────┬────────┬───┬──────────┬───────────┬──────┬─────────────┐
│ depictio_run ┆ sample     ┆ cell        ┆ medbin ┆ … ┆ nb_p     ┆ nb_r      ┆ nb_a ┆ bam         │
│ _id          ┆ ---        ┆ ---         ┆ ---    ┆   ┆ ---      ┆ ---       ┆ ---  ┆ ---         │
│ ---          ┆ str        ┆ str         ┆ i64    ┆   ┆ f64      ┆ f64       ┆ f64  ┆ str         │
│ str          ┆            ┆             ┆        ┆   ┆          ┆           ┆      ┆             │
╞══════════════╪════════════╪═════════════╪════════╪═══╪══════════╪═══════════╪══════╪═════════════╡
│ 2019-09-11-H ┆ HG01114x02 ┆ HG01114x02P ┆ 23     ┆ … ┆ 0.008158 ┆ 0.196344  ┆ 0.1  ┆ /scratch/tw │
│ TN7CAFXY     ┆            ┆ E20301      ┆        ┆   ┆          ┆           ┆      ┆ eber/DATA/M │
│              ┆            ┆             ┆        ┆   ┆          ┆           ┆      ┆ C_DATA/STO… │
│ 2019-09-11-H ┆ HG01114x02 ┆ HG01114x02P ┆ 5      ┆ … ┆ 0.008158 ┆ 0.05

In [7]:
from io import BytesIO
import boto3
import polars as pl
import os

# Set environment variables for MinIO access
os.environ["AWS_ACCESS_KEY_ID"] = "minio"
os.environ["AWS_SECRET_ACCESS_KEY"] = "minio123"
os.environ["AWS_ENDPOINT_URL"] = "http://localhost:9000"  # This might need to be AWS_S3_ENDPOINT_URL depending on the version and setup
os.environ["AWS_REGION"] = "us-east-1"  # This can be a placeholder value


object_key = 's3://depictio-bucket/64a842842bf4fa7deaa3dbed/65c4ef0f26d99f46c993a5af/65c4ef0f26d99f46c993a5b0/1-ea34b2f8-4b6c-455f-b3ca-1ae0519c792f-0.parquet'  # Name of your parquet file


def construct_parquet_query(object_key, user_input):
    """
    Constructs a lazy query for accessing and filtering a Parquet file based on user input,
    including support for categorical and string pattern matching queries.
    """
    query = pl.scan_parquet(object_key)
    
    # Apply filters if any
    if "filters" in user_input:
        for f in user_input["filters"]:
            column = pl.col(f["column"])
            if f["operator"] == "==":
                query = query.filter(column == f["value"])
            elif f["operator"] == ">":
                query = query.filter(column > f["value"])
            elif f["operator"] == "<":
                query = query.filter(column < f["value"])
            elif f["operator"] == ">=":
                query = query.filter(column >= f["value"])
            elif f["operator"] == "<=":
                query = query.filter(column <= f["value"])
            elif f["operator"] == "isin":
                query = query.filter(column.is_in(f["values"]))  # Assuming 'values' is a list
            elif f["operator"] == "contains":
                # Ensure the column is of type str before applying str.contains
                query = query.filter(column.str.contains(f["pattern"]))
            # Add more operators as needed

    # Select columns if specified
    if "select_columns" in user_input:
        query = query.select(user_input["select_columns"])

    return query



user_input = {
    "filters": [
        {"column": "pass1", "operator": "==", "value": 1},
        {"column": "cell", "operator": "isin", "values": ["HG01114x02PE20301", "HG01114x02PE20302", "HG02106x02PE20390", "HG02106x02PE20392"]},
        {"column": "cell", "operator": "contains", "pattern": "HG01.*"}
    ],
    "select_columns": ["cell", "mapped", "pass1"]
}


query = construct_parquet_query(object_key, user_input)



# Now, collect the results to trigger the actual computation
try:
    df = query.collect()
    print(df)
except Exception as e:  # Catching a more general exception as boto3 exceptions won't be raised here
    print(f"An error occurred: {e}")


shape: (2, 3)
┌───────────────────┬─────────┬───────┐
│ cell              ┆ mapped  ┆ pass1 │
│ ---               ┆ ---     ┆ ---   │
│ str               ┆ i64     ┆ i64   │
╞═══════════════════╪═════════╪═══════╡
│ HG01114x02PE20301 ┆ 1160663 ┆ 1     │
│ HG01114x02PE20302 ┆ 314705  ┆ 1     │
└───────────────────┴─────────┴───────┘


In [4]:
import os
import polars as pl

# Set environment variables for MinIO access
os.environ["AWS_ACCESS_KEY_ID"] = "minio"
os.environ["AWS_SECRET_ACCESS_KEY"] = "minio123"
os.environ["AWS_ENDPOINT_URL"] = "http://localhost:9000"  # This might need to be AWS_S3_ENDPOINT_URL depending on the version and setup
os.environ["AWS_REGION"] = "us-east-1"  # This can be a placeholder value

# Assuming the Delta table is located at this path in your MinIO bucket
delta_table_path = "s3://depictio-bucket/64a842842bf4fa7deaa3dbed/65c4ef0f26d99f46c993a5af/65c4ef0f26d99f46c993a5b0/"

# Attempt to read the Delta table using Polars
try:
    df = pl.read_delta(delta_table_path)
    print(df)
except Exception as e:
    print(f"Failed to read Delta table: {e}")


Failed to read Delta table: Generic S3 error: Error after 0 retries in 2.458µs, max_retries:10, retry_timeout:180s, source:builder error for url (http://localhost:9000/depictio-bucket/64a842842bf4fa7deaa3dbed/65c4ef0f26d99f46c993a5af/65c4ef0f26d99f46c993a5b0/_delta_log/_last_checkpoint): URL scheme is not allowed


In [ ]:
import os
import polars as pl

# Set environment variables for MinIO access
os.environ["AWS_ACCESS_KEY_ID"] = "minio"
os.environ["AWS_SECRET_ACCESS_KEY"] = "minio123"
os.environ["AWS_S3_ENDPOINT_URL"] = "http://localhost:9000"  # This might need to be AWS_S3_ENDPOINT_URL depending on the version and setup
os.environ["AWS_REGION"] = "us-east-1"  # This can be a placeholder value

# Assuming the Delta table is located at this path in your MinIO bucket
delta_table_path = "s3://depictio-bucket/64a842842bf4fa7deaa3dbed/65c4ef0f26d99f46c993a5af/65c4ef0f26d99f46c993a5b0/"

# Attempt to read the Delta table using Polars
try:
    df = pl.read_delta(delta_table_path)
    print(df)
except Exception as e:
    print(f"Failed to read Delta table: {e}")


Failed to read Delta table: Generic S3 error: Error after 0 retries in 2.166µs, max_retries:10, retry_timeout:180s, source:builder error for url (http://localhost:9000/depictio-bucket/64a842842bf4fa7deaa3dbed/65c4ef0f26d99f46c993a5af/65c4ef0f26d99f46c993a5b0/_delta_log/_last_checkpoint): URL scheme is not allowed


In [3]:
import polars as pl

df = pl.DataFrame(
    {
        "foo": [1, 2, 3, 4, 5],
        "bar": [6, 7, 8, 9, 10],
        "ham": ["a", "b", "c", "d", "e"],
    }
)
import os 
os.environ["AWS_ACCESS_KEY_ID"] = "minio"
os.environ["AWS_SECRET_ACCESS_KEY"] = "minio123"
os.environ["AWS_S3_ENDPOINT_URL"] = "http://localhost:9000"  # This might need to be AWS_S3_ENDPOINT_URL depending on the version and setup
os.environ["AWS_REGION"] = "us-east-1"  # This can be a placeholder value


table_path = "s3://depictio-bucket/delta-table/"
df.write_delta(
    table_path,
    storage_options={
        "AWS_REGION": "us-east-1",
        # "AWS_ACCESS_KEY_ID": "your_access_key",
        # "AWS_SECRET_ACCESS_KEY": "your_secret_key",
    },
) 

OSError: Generic S3 error: Client error with status 403 Forbidden: <?xml version="1.0" encoding="UTF-8"?>
<Error><Code>InvalidAccessKeyId</Code><Message>The AWS Access Key Id you provided does not exist in our records.</Message><AWSAccessKeyId>minio</AWSAccessKeyId><RequestId>DZCNMWBFDE4NXHD8</RequestId><HostId>YDdUErq5det/8IEKAggfDWVX3JpQmrGfmXC2St7ej/KGXvS6hRd/ybycRv2PQOFzdJrhHT+0pPs=</HostId></Error>

In [9]:
pl.show_versions()

--------Version info---------
Polars:               0.20.7
Index type:           UInt32
Platform:             macOS-14.3-arm64-arm-64bit
Python:               3.11.7 | packaged by conda-forge | (main, Dec 23 2023, 14:38:07) [Clang 16.0.6 ]

----Optional dependencies----
adbc_driver_manager:  <not installed>
cloudpickle:          <not installed>
connectorx:           <not installed>
deltalake:            0.15.1
fsspec:               2024.2.0
gevent:               <not installed>
hvplot:               <not installed>
matplotlib:           <not installed>
numpy:                1.26.3
openpyxl:             <not installed>
pandas:               2.2.0
pyarrow:              15.0.0
pydantic:             1.10.10
pyiceberg:            <not installed>
pyxlsb:               <not installed>
sqlalchemy:           <not installed>
xlsx2csv:             <not installed>
xlsxwriter:           <not installed>


In [14]:
from pymongo import MongoClient
from bson.objectid import ObjectId

client = MongoClient("mongodb://localhost:27018")
db = client["depictioDB"]
files_collection = db["files_collection"]

# Correctly reference the ObjectId for data_collection._id
result = files_collection.delete_many({"data_collection._id": ObjectId("65c4ef0f26d99f46c993a5b2")})

print(f"Number of documents deleted: {result.deleted_count}")


Number of documents deleted: 7604


In [ ]:
from pymongo import MongoClient
from bson.objectid import ObjectId

client = MongoClient("mongodb://localhost:27018")
db = client["depictioDB"]
files_collection = db["files_collection"]

# Correctly reference the ObjectId for data_collection._id
result = files_collection.find({"data_collection._id": ObjectId("65c4ef0f26d99f46c993a5b2")})

for file in result:
    print(file)


{'_id': ObjectId('65cb3f805b1b281656a3cdcd'), 'file_location': '/Users/tweber/Data/mosaicatcher-pipeline/2019-09-11-HTN7CAFXY/HG01114x02/plots/JBROWSE/HG01114x02PE20356-SV.bed.gz.tbi', 'S3_location': None, 'filename': 'HG01114x02PE20356-SV.bed.gz.tbi', 'creation_time': datetime.datetime(2024, 1, 29, 11, 5, 44), 'modification_time': datetime.datetime(2024, 1, 24, 7, 1, 31), 'data_collection': {'_id': ObjectId('65c4ef0f26d99f46c993a5b2'), 'data_collection_tag': 'SV_calls', 'description': 'BED files containing SV calls generated by MosaiCatcher', 'config': {'type': 'Genome Browser', 'regex': '.*.bed.gz', 'format': 'BED', 'polars_kwargs': {}, 'keep_columns': [], 'join': None, 'jbrowse_params': {'category': 'SV calls', 'assemblyName': 'hg38'}, 'index_extension': 'tbi'}, 'deltaTable': None, 'columns': None}, 'run_id': '2019-09-11-HTN7CAFXY', 'aggregated': False}
{'_id': ObjectId('65cb3f9957c1df048dbacec0'), 'file_location': '/Users/tweber/Data/mosaicatcher-pipeline/2019-09-11-HTN7CAFXY/HG011